In [1]:
%load_ext Cython

In [118]:
%%cython
from libc.math cimport sqrt
import numpy as np

def _circumcircle_radius(pt1, pt2, pt3):
    
    cdef:
        double x0
        double y0
        double x1
        double y1
        double x2
        double y2
        
    x0 = pt1[0]
    y0 = pt1[1]
    x1 = pt2[0]
    y1 = pt2[1]
    x2 = pt3[0]
    y2 = pt3[1]
    
    return c_circumcircle_radius(x0, y0, x1, y1, x2, y2)

cdef double c_dist_2(double x0, double y0, double x1, double y1):

    cdef:
        double d0
        double d1

    d0 = x1 - x0
    d1 = y1 - y0
    
    return d0 * d0 + d1 * d1

cdef double c_circumcircle_radius(double x0, double y0, double x1, 
                                  double y1, double x2, double y2):

    cdef:
        double a
        double b
        double c
        double s
        double prod
        double prod2
        double radius

    a = c_dist_2(x0, y0, x1, y1)
    b = c_dist_2(x1, y1, x2, y2)
    c = c_dist_2(x2, y2, x0, y0)
    
    s = (a + b + c) * 0.5
    
    prod = (2 * np.cross((p1 - p2), (p2 - p3)))[2])**2
    prod2 = a*b*c
    
    radius = prod2 * prod2 / (16*prod)
    
    return radius

def _circumcenter(pt1, pt2, pt3):
        
    cdef:
        double x0
        double y0
        double x1
        double y1
        double x2
        double y2
        double cx
        double cy
        
    x0 = pt1[0]
    y0 = pt1[1]
    x1 = pt2[0]
    y1 = pt2[1]
    x2 = pt3[0]
    y2 = pt3[1]
        
    c_circumcenter(&cx, &cy, x0, y0, x1, y1, x2, y2)
    
    return cx, cy

cdef void c_circumcenter(double * cx, double * cy, double x0, double y0, double x1, 
                         double y1, double x2, double y2):

    cdef:
        double bc_y_diff
        double ca_y_diff
        double ab_y_diff
        double d_inv
        double a_mag
        double b_mag
        double c_mag

    bc_y_diff = y1 - y2
    ca_y_diff = y2 - y0
    ab_y_diff = y0 - y1
    
    d_inv = 0.5 / (x0 * bc_y_diff + x1 * ca_y_diff + x2 * ab_y_diff)
    
    a_mag = x0 * x0 + y0 * y0
    b_mag = x1 * x1 + y1 * y1
    c_mag = x2 * x2 + y2 * y2
    
    cx[0] = (a_mag * bc_y_diff + b_mag * ca_y_diff + c_mag * ab_y_diff) * d_inv
    cy[0] = (a_mag * (x2 - x1) + b_mag * (x0 - x2) + c_mag * (x1 - x0)) * d_inv

In [119]:
%timeit _circumcircle_radius(p1, p2, p3)

Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError:

10000 loops, best of 3: 24.1 µs per loop


ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circu

In [79]:
def _find_natural_neighbors(tri, grid_points):

    tree = cKDTree(grid_points)

    in_triangulation = tri.find_simplex(tree.data) >= 0

    triangle_info = dict()

    members = dict((key, []) for key in range(len(tree.data)))

    for i in range(len(tri.simplices)):

        ps = tri.points[tri.simplices[i]]
        print(ps)
        cc = _circumcenter(*ps)
        r = _circumcircle_radius(*ps)

        triangle_info[i] = {'cc': cc, 'r': r}

        qualifiers = tree.query_ball_point(cc, r)

        for qualifier in qualifiers:
            if in_triangulation[qualifier]:
                members[qualifier].append(i)

    return members, triangle_info

In [80]:
x = list(range(0, 20, 4))
y = list(range(0, 20, 4))
gx, gy = np.meshgrid(x, y)
pts = np.vstack([gx.ravel(), gy.ravel()]).T
tri = Delaunay(pts)

test_points = np.array([[2, 2], [5, 10], [12, 13.4], [12, 8], [20, 20]])

%timeit _find_natural_neighbors(tri, test_points)

[[ 4.  0.]
 [ 0.  4.]
 [ 0.  0.]]
[[ 0.  4.]
 [ 4.  0.]
 [ 4.  4.]]
[[ 16.   4.]
 [ 12.   0.]
 [ 16.   0.]]
[[ 12.   0.]
 [ 16.   4.]
 [ 12.   4.]]
[[ 4.  0.]
 [ 8.  4.]
 [ 4.  4.]]
[[ 8.  4.]
 [ 4.  0.]
 [ 8.  0.]]
[[  8.   4.]
 [ 12.   0.]
 [ 12.   4.]]
[[ 12.   0.]
 [  8.   4.]
 [  8.   0.]]
[[  0.  12.]
 [  4.  16.]
 [  0.  16.]]
[[  4.  16.]
 [  0.  12.]
 [  4.  12.]]
[[ 8.  4.]
 [ 4.  8.]
 [ 4.  4.]]
[[ 4.  8.]
 [ 8.  4.]
 [ 8.  8.]]
[[ 4.  8.]
 [ 0.  4.]
 [ 4.  4.]]
[[ 0.  4.]
 [ 4.  8.]
 [ 0.  8.]]
[[  0.  12.]
 [  4.   8.]
 [  4.  12.]]
[[  4.   8.]
 [  0.  12.]
 [  0.   8.]]
[[ 12.  16.]
 [ 16.  12.]
 [ 16.  16.]]
[[ 16.  12.]
 [ 12.  16.]
 [ 12.  12.]]
[[  8.   4.]
 [ 12.   8.]
 [  8.   8.]]
[[ 12.   8.]
 [  8.   4.]
 [ 12.   4.]]
[[ 16.   4.]
 [ 12.   8.]
 [ 12.   4.]]
[[ 12.   8.]
 [ 16.   4.]
 [ 16.   8.]]
[[ 12.   8.]
 [ 16.  12.]
 [ 12.  12.]]
[[ 16.  12.]
 [ 12.   8.]
 [ 16.   8.]]
[[  4.   8.]
 [  8.  12.]
 [  4.  12.]]
[[  8.  12.]
 [  4.   8.]
 [  8.   8.]]
[[  8.  

Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError:

[[ 4.  0.]
 [ 0.  4.]
 [ 0.  0.]]
[[ 0.  4.]
 [ 4.  0.]
 [ 4.  4.]]
[[ 16.   4.]
 [ 12.   0.]
 [ 16.   0.]]
[[ 12.   0.]
 [ 16.   4.]
 [ 12.   4.]]
[[ 4.  0.]
 [ 8.  4.]
 [ 4.  4.]]
[[ 8.  4.]
 [ 4.  0.]
 [ 8.  0.]]
[[  8.   4.]
 [ 12.   0.]
 [ 12.   4.]]
[[ 12.   0.]
 [  8.   4.]
 [  8.   0.]]
[[  0.  12.]
 [  4.  16.]
 [  0.  16.]]
[[  4.  16.]
 [  0.  12.]
 [  4.  12.]]
[[ 8.  4.]
 [ 4.  8.]
 [ 4.  4.]]
[[ 4.  8.]
 [ 8.  4.]
 [ 8.  8.]]
[[ 4.  8.]
 [ 0.  4.]
 [ 4.  4.]]
[[ 0.  4.]
 [ 4.  8.]
 [ 0.  8.]]
[[  0.  12.]
 [  4.   8.]
 [  4.  12.]]
[[  4.   8.]
 [  0.  12.]
 [  0.   8.]]
[[ 12.  16.]
 [ 16.  12.]
 [ 16.  16.]]
[[ 16.  12.]
 [ 12.  16.]
 [ 12.  12.]]
[[  8.   4.]
 [ 12.   8.]
 [  8.   8.]]
[[ 12.   8.]
 [  8.   4.]
 [ 12.   4.]]
[[ 16.   4.]
 [ 12.   8.]
 [ 12.   4.]]
[[ 12.   8.]
 [ 16.   4.]
 [ 16.   8.]]
[[ 12.   8.]
 [ 16.  12.]
 [ 12.  12.]]
[[ 16.  12.]
 [ 12.   8.]
 [ 16.   8.]]
[[  4.   8.]
 [  8.  12.]
 [  4.  12.]]
[[  8.  12.]
 [  4.   8.]
 [  8.   8.]]
[[  8.  

Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError:

[[ 12.   8.]
 [  8.   4.]
 [ 12.   4.]]
[[ 16.   4.]
 [ 12.   8.]
 [ 12.   4.]]
[[ 12.   8.]
 [ 16.   4.]
 [ 16.   8.]]
[[ 12.   8.]
 [ 16.  12.]
 [ 12.  12.]]
[[ 16.  12.]
 [ 12.   8.]
 [ 16.   8.]]
[[  4.   8.]
 [  8.  12.]
 [  4.  12.]]
[[  8.  12.]
 [  4.   8.]
 [  8.   8.]]
[[  8.  12.]
 [ 12.   8.]
 [ 12.  12.]]
[[ 12.   8.]
 [  8.  12.]
 [  8.   8.]]
[[  8.  12.]
 [  4.  16.]
 [  4.  12.]]
[[  4.  16.]
 [  8.  12.]
 [  8.  16.]]
[[ 12.  16.]
 [  8.  12.]
 [ 12.  12.]]
[[  8.  12.]
 [ 12.  16.]
 [  8.  16.]]
[[ 4.  0.]
 [ 0.  4.]
 [ 0.  0.]]
[[ 0.  4.]
 [ 4.  0.]
 [ 4.  4.]]
[[ 16.   4.]
 [ 12.   0.]
 [ 16.   0.]]
[[ 12.   0.]
 [ 16.   4.]
 [ 12.   4.]]
[[ 4.  0.]
 [ 8.  4.]
 [ 4.  4.]]
[[ 8.  4.]
 [ 4.  0.]
 [ 8.  0.]]
[[  8.   4.]
 [ 12.   0.]
 [ 12.   4.]]
[[ 12.   0.]
 [  8.   4.]
 [  8.   0.]]
[[  0.  12.]
 [  4.  16.]
 [  0.  16.]]
[[  4.  16.]
 [  0.  12.]
 [  4.  12.]]
[[ 8.  4.]
 [ 4.  8.]
 [ 4.  4.]]
[[ 4.  8.]
 [ 8.  4.]
 [ 8.  8.]]
[[ 4.  8.]
 [ 0.  4.]
 [ 4.  4.]]
[[

Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError: float division
Exception ignored in: '_cython_magic_16c77056c22ca260521ad86d65e42a64.c_circumcircle_radius'
ZeroDivisionError:

In [107]:
from scipy.spatial.distance import euclidean

p1 = np.array([0, 10, 0])
p2 = np.array([10, 10, 0])
p3 = np.array([10, 0, 0])

def dist_lin(p1, p2, p3):
    
    a = np.linalg.norm(p1 - p2)
    b = np.linalg.norm(p2 - p3)
    c = np.linalg.norm(p3 - p1)

    return (a*b*c) / (2 * np.cross((p1 - p2), (p2 - p3)))[2]
    
    



In [111]:
%timeit _dist_2(p1, p2, p3)

TypeError: _dist_2() takes exactly 4 positional arguments (3 given)